<a href="https://colab.research.google.com/github/Zaka123456/MRP/blob/main/Weather_features_fetching.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
pip install requests pandas numpy matplotlib seaborn scipy requests-cache retry-requests

   ---------------------------------------- 0.0/11.0 MB ? eta -:--:--
   ----------------- ---------------------- 4.7/11.0 MB 26.0 MB/s eta 0:00:01
   -------------------------------------- - 10.5/11.0 MB 26.0 MB/s eta 0:00:01
   ---------------------------------------- 11.0/11.0 MB 23.8 MB/s eta 0:00:00
   ---------------------------------------- 0.0/12.7 MB ? eta -:--:--
   ------------ --------------------------- 3.9/12.7 MB 19.1 MB/s eta 0:00:01
   ------------------------------ --------- 9.7/12.7 MB 23.0 MB/s eta 0:00:01
   ---------------------------------------- 12.7/12.7 MB 22.9 MB/s eta 0:00:00
   ---------------------------------------- 0.0/8.1 MB ? eta -:--:--
   --------------------------- ------------ 5.5/8.1 MB 28.2 MB/s eta 0:00:01
   ---------------------------------------- 8.1/8.1 MB 25.9 MB/s eta 0:00:00
   ---------------------------------------- 0.0/38.4 MB ? eta -:--:--
   ---- ----------------------------------- 4.5/38.4 MB 23.5 MB/s eta 0:00:02
   --------- -----

In [ ]:
# ======== IMPORTS ========
import os
import sys
import time
import math
import random
import requests
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime, timedelta
from scipy import stats


In [ ]:
# ================================
# Visual Crossing Weather Fetcher (2017)
# Batch processing (25 coordinates at a time)
# ================================



# --- STEP 1: Configuration ---
INPUT_CSV = "unique_lat_lon.csv"
OUTPUT_CSV = "visualcrossing_weather_2017.csv"
BATCH_SIZE = 25
YEAR = 2017

API_KEY = "BLRV9J7HVT4KS2DZ9KM4AUWWJ"

BASE_URL = (
    "https://weather.visualcrossing.com/VisualCrossingWebServices/rest/services/timeline/"
    "{lat},{lon}/{start_date}/{end_date}"
    "?unitGroup=us&elements=datetime,latitude,longitude,tempmax,tempmin,temp,humidity,precip,"
    "preciptype,snow,windspeed,cloudcover,solarradiation&include=days&key={api_key}&contentType=json"
)

# --- STEP 2: Function to fetch weather data for one location-year ---
def fetch_visualcrossing(lat, lon, year):
    start_date = f"{year}-01-01"
    end_date = f"{year}-12-31"
    url = BASE_URL.format(lat=lat, lon=lon, start_date=start_date, end_date=end_date, api_key=API_KEY)

    try:
        response = requests.get(url, timeout=60)
        response.raise_for_status()
        data = response.json()

        # Explicitly log if missing daily data
        if "days" not in data or not data["days"]:
            return f"EMPTY or MISSING daily section for {lat},{lon}"

        df = pd.json_normalize(data["days"])
        df["latitude"] = lat
        df["longitude"] = lon
        df["year"] = year
        return df

    except Exception as e:
        return f"ERROR: {e}"

# --- STEP 3: Load coordinates ---
df_coords = pd.read_csv(INPUT_CSV)
df_coords[['latitude', 'longitude']] = df_coords['lat_lon'].str.split(',', expand=True).astype(float)

# --- STEP 4: Batch processing (25 at a time) ---
num_coords = len(df_coords)
for start in range(0, num_coords, BATCH_SIZE):
    batch = df_coords.iloc[start:start + BATCH_SIZE]
    print(f"\nProcessing batch {start+1} to {start + len(batch)} of {num_coords}")

    batch_results = []
    for idx, row in batch.iterrows():
        lat = row["latitude"]
        lon = row["longitude"]

        print(f"Fetching weather for {lat},{lon} ({YEAR})...")
        result = fetch_visualcrossing(lat, lon, YEAR)

        if isinstance(result, pd.DataFrame):
            batch_results.append(result)
            print(f"✅ Data retrieved: {lat},{lon}")
        else:
            print(f"⚠️ Failed: {lat},{lon} -> {result}")

        time.sleep(1)  # To avoid hitting rate limits

    # Save results for this batch
    if batch_results:
        final_batch_df = pd.concat(batch_results, ignore_index=True)
        header_flag = not os.path.exists(OUTPUT_CSV)
        final_batch_df.to_csv(OUTPUT_CSV, mode="a", index=False, header=header_flag)
        print(f"Saved {len(final_batch_df)} records for this batch")

print("\nAll batches for 2017 processed and saved!")



Processing batch 1 to 25 of 11835
Fetching weather for 18.2514534,-66.03705597 (2017)...
✅ Data retrieved: 18.2514534,-66.03705597
Fetching weather for 18.27945137,-66.0370636 (2017)...
✅ Data retrieved: 18.27945137,-66.0370636
Fetching weather for 37.29223251,-121.881279 (2017)...
✅ Data retrieved: 37.29223251,-121.881279
Fetching weather for 34.12594605,-118.2910156 (2017)...
✅ Data retrieved: 34.12594605,-118.2910156
Fetching weather for 18.25376892,-66.03704834 (2017)...
✅ Data retrieved: 18.25376892,-66.03704834
Fetching weather for 43.01396942,-78.87906647 (2017)...
✅ Data retrieved: 43.01396942,-78.87906647
Fetching weather for 18.24253845,-66.03705597 (2017)...
✅ Data retrieved: 18.24253845,-66.03705597
Fetching weather for 25.92886925,-80.16287231 (2017)...
✅ Data retrieved: 25.92886925,-80.16287231
Fetching weather for 18.23322296,-66.03705597 (2017)...
✅ Data retrieved: 18.23322296,-66.03705597
Fetching weather for 37.77399063,-121.966629 (2017)...
✅ Data retrieved: 37.7739

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\1578042105.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 26 to 50 of 11835
Fetching weather for 18.26163292,-66.03705597 (2017)...
✅ Data retrieved: 18.26163292,-66.03705597
Fetching weather for 41.23545456,-75.86985779 (2017)...
✅ Data retrieved: 41.23545456,-75.86985779
Fetching weather for 18.27022362,-66.0370636 (2017)...
✅ Data retrieved: 18.27022362,-66.0370636
Fetching weather for 41.86886215,-84.57365418 (2017)...
✅ Data retrieved: 41.86886215,-84.57365418
Fetching weather for 33.90942383,-118.1253586 (2017)...
✅ Data retrieved: 33.90942383,-118.1253586
Fetching weather for 18.27526093,-66.0370636 (2017)...
✅ Data retrieved: 18.27526093,-66.0370636
Fetching weather for 41.86544037,-88.10990143 (2017)...
✅ Data retrieved: 41.86544037,-88.10990143
Fetching weather for 18.28713608,-66.03705597 (2017)...
✅ Data retrieved: 18.28713608,-66.03705597
Fetching weather for 42.39110184,-83.13121796 (2017)...
✅ Data retrieved: 42.39110184,-83.13121796
Fetching weather for 32.86539459,-96.868583

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\1578042105.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 51 to 75 of 11835
Fetching weather for 18.02536774,-66.61303711 (2017)...
✅ Data retrieved: 18.02536774,-66.61303711
Fetching weather for 18.27383804,-66.37063599 (2017)...
✅ Data retrieved: 18.27383804,-66.37063599
Fetching weather for 18.2848053,-66.37059021 (2017)...
✅ Data retrieved: 18.2848053,-66.37059021
Fetching weather for 18.29496765,-66.37050629 (2017)...
✅ Data retrieved: 18.29496765,-66.37050629
Fetching weather for 18.25571251,-66.37050629 (2017)...
✅ Data retrieved: 18.25571251,-66.37050629
Fetching weather for 18.23466301,-66.37059784 (2017)...
✅ Data retrieved: 18.23466301,-66.37059784
Fetching weather for 18.26268196,-66.37049866 (2017)...
✅ Data retrieved: 18.26268196,-66.37049866
Fetching weather for 18.28279495,-66.37055969 (2017)...
✅ Data retrieved: 18.28279495,-66.37055969
Fetching weather for 18.27466202,-66.37058258 (2017)...
✅ Data retrieved: 18.27466202,-66.37058258
Fetching weather for 18.2689991,-66.37049

...

Saved 9125 records for this batch

Processing batch 10251 to 10275 of 11835
Fetching weather for 18.28136253,-66.03704834 (2017)...
✅ Data retrieved: 18.28136253,-66.03704834
Fetching weather for 18.22372437,-66.03705597 (2017)...
✅ Data retrieved: 18.22372437,-66.03705597
Fetching weather for 18.23401642,-66.03704834 (2017)...
✅ Data retrieved: 18.23401642,-66.03704834
Fetching weather for 18.29497719,-66.0370636 (2017)...
✅ Data retrieved: 18.29497719,-66.0370636
Fetching weather for 18.2678833,-66.03705597 (2017)...
✅ Data retrieved: 18.2678833,-66.03705597
Fetching weather for 18.23389816,-66.03705597 (2017)...
✅ Data retrieved: 18.23389816,-66.03705597
Fetching weather for 18.28822899,-66.03705597 (2017)...
✅ Data retrieved: 18.28822899,-66.03705597
Fetching weather for 18.22524262,-66.03705597 (2017)...
✅ Data retrieved: 18.22524262,-66.03705597
Fetching weather for 18.27915955,-66.0370636 (2017)...
✅ Data retrieved: 18.27915955,-66.0370636
Fetching weather for 18.25095177,-66.03

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\1578042105.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 11076 to 11100 of 11835
Fetching weather for 18.24691773,-66.37050629 (2017)...
✅ Data retrieved: 18.24691773,-66.37050629
Fetching weather for 18.24759674,-66.02526856 (2017)...
✅ Data retrieved: 18.24759674,-66.02526856
Fetching weather for 40.64011765,-73.94268036 (2017)...
✅ Data retrieved: 40.64011765,-73.94268036
Fetching weather for 18.29045868,-66.37049866 (2017)...
✅ Data retrieved: 18.29045868,-66.37049866
Fetching weather for 18.28666687,-66.37056732 (2017)...
✅ Data retrieved: 18.28666687,-66.37056732
Fetching weather for 18.27922058,-66.37059021 (2017)...
✅ Data retrieved: 18.27922058,-66.37059021
Fetching weather for 18.25029755,-66.03705597 (2017)...
✅ Data retrieved: 18.25029755,-66.03705597
Fetching weather for 18.22234154,-66.03705597 (2017)...
✅ Data retrieved: 18.22234154,-66.03705597
Fetching weather for 18.272295,-66.03704834 (2017)...
✅ Data retrieved: 18.272295,-66.03704834
Fetching weather for 18.29675102,-66.

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\1578042105.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 11551 to 11575 of 11835
Fetching weather for 34.04514694,-118.2484818 (2017)...
✅ Data retrieved: 34.04514694,-118.2484818
Fetching weather for 38.40907288,-121.4195862 (2017)...
✅ Data retrieved: 38.40907288,-121.4195862
Fetching weather for 28.58658218,-81.28829193 (2017)...
✅ Data retrieved: 28.58658218,-81.28829193
Fetching weather for 34.00076294,-117.8856812 (2017)...
✅ Data retrieved: 34.00076294,-117.8856812
Fetching weather for 41.89596176,-87.69457245 (2017)...
✅ Data retrieved: 41.89596176,-87.69457245
Fetching weather for 18.20450401,-66.03704834 (2017)...
✅ Data retrieved: 18.20450401,-66.03704834
Fetching weather for 18.28610039,-66.03705597 (2017)...
✅ Data retrieved: 18.28610039,-66.03705597
Fetching weather for 18.26597595,-66.0370636 (2017)...
✅ Data retrieved: 18.26597595,-66.0370636
Fetching weather for 18.21594429,-66.03705597 (2017)...
✅ Data retrieved: 18.21594429,-66.03705597
Fetching weather for 18.27234268,-6

In [ ]:
# ================================
# Visual Crossing Weather Fetcher (2016)
# Batch processing (25 coordinates at a time)
# ================================



# --- STEP 1: Configuration ---
INPUT_CSV = "unique_lat_lon.csv"
OUTPUT_CSV = "visualcrossing_weather_2016.csv"
BATCH_SIZE = 25
YEAR = 2016

API_KEY = "BLRV9J7HVT4KS2DZ9KM4AUWWJ"

BASE_URL = (
    "https://weather.visualcrossing.com/VisualCrossingWebServices/rest/services/timeline/"
    "{lat},{lon}/{start_date}/{end_date}"
    "?unitGroup=us&elements=datetime,latitude,longitude,tempmax,tempmin,temp,humidity,precip,"
    "preciptype,snow,windspeed,cloudcover,solarradiation&include=days&key={api_key}&contentType=json"
)

# --- STEP 2: Function to fetch weather data for one location-year ---
def fetch_visualcrossing(lat, lon, year):
    start_date = f"{year}-01-01"
    end_date = f"{year}-12-31"
    url = BASE_URL.format(lat=lat, lon=lon, start_date=start_date, end_date=end_date, api_key=API_KEY)

    try:
        response = requests.get(url, timeout=60)
        response.raise_for_status()
        data = response.json()

        # Explicitly log if missing daily data
        if "days" not in data or not data["days"]:
            return f"EMPTY or MISSING daily section for {lat},{lon}"

        df = pd.json_normalize(data["days"])
        df["latitude"] = lat
        df["longitude"] = lon
        df["year"] = year
        return df

    except Exception as e:
        return f"ERROR: {e}"

# --- STEP 3: Load coordinates ---
df_coords = pd.read_csv(INPUT_CSV)
df_coords[['latitude', 'longitude']] = df_coords['lat_lon'].str.split(',', expand=True).astype(float)

# --- STEP 4: Batch processing (25 at a time) ---
num_coords = len(df_coords)
for start in range(0, num_coords, BATCH_SIZE):
    batch = df_coords.iloc[start:start + BATCH_SIZE]
    print(f"\nProcessing batch {start+1} to {start + len(batch)} of {num_coords}")

    batch_results = []
    for idx, row in batch.iterrows():
        lat = row["latitude"]
        lon = row["longitude"]

        print(f"Fetching weather for {lat},{lon} ({YEAR})...")
        result = fetch_visualcrossing(lat, lon, YEAR)

        if isinstance(result, pd.DataFrame):
            batch_results.append(result)
            print(f"✅ Data retrieved: {lat},{lon}")
        else:
            print(f"⚠️ Failed: {lat},{lon} -> {result}")

        time.sleep(1)  # To avoid hitting rate limits

    # Save results for this batch
    if batch_results:
        final_batch_df = pd.concat(batch_results, ignore_index=True)
        header_flag = not os.path.exists(OUTPUT_CSV)
        final_batch_df.to_csv(OUTPUT_CSV, mode="a", index=False, header=header_flag)
        print(f"Saved {len(final_batch_df)} records for this batch")

print("\nAll batches for 2016 processed and saved!")


Processing batch 1 to 25 of 11835
Fetching weather for 18.2514534,-66.03705597 (2016)...
✅ Data retrieved: 18.2514534,-66.03705597
Fetching weather for 18.27945137,-66.0370636 (2016)...
✅ Data retrieved: 18.27945137,-66.0370636
Fetching weather for 37.29223251,-121.881279 (2016)...
✅ Data retrieved: 37.29223251,-121.881279
Fetching weather for 34.12594605,-118.2910156 (2016)...
✅ Data retrieved: 34.12594605,-118.2910156
Fetching weather for 18.25376892,-66.03704834 (2016)...
✅ Data retrieved: 18.25376892,-66.03704834
Fetching weather for 43.01396942,-78.87906647 (2016)...
✅ Data retrieved: 43.01396942,-78.87906647
Fetching weather for 18.24253845,-66.03705597 (2016)...
✅ Data retrieved: 18.24253845,-66.03705597
Fetching weather for 25.92886925,-80.16287231 (2016)...
✅ Data retrieved: 25.92886925,-80.16287231
Fetching weather for 18.23322296,-66.03705597 (2016)...
✅ Data retrieved: 18.23322296,-66.03705597
Fetching weather for 37.77399063,-121.966629 (2016)...
✅ Data retrieved: 37.7739

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\297163049.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9150 records for this batch

Processing batch 26 to 50 of 11835
Fetching weather for 18.26163292,-66.03705597 (2016)...
✅ Data retrieved: 18.26163292,-66.03705597
Fetching weather for 41.23545456,-75.86985779 (2016)...
✅ Data retrieved: 41.23545456,-75.86985779
Fetching weather for 18.27022362,-66.0370636 (2016)...
✅ Data retrieved: 18.27022362,-66.0370636
Fetching weather for 41.86886215,-84.57365418 (2016)...
✅ Data retrieved: 41.86886215,-84.57365418
Fetching weather for 33.90942383,-118.1253586 (2016)...
✅ Data retrieved: 33.90942383,-118.1253586
Fetching weather for 18.27526093,-66.0370636 (2016)...
✅ Data retrieved: 18.27526093,-66.0370636
Fetching weather for 41.86544037,-88.10990143 (2016)...
✅ Data retrieved: 41.86544037,-88.10990143
Fetching weather for 18.28713608,-66.03705597 (2016)...
✅ Data retrieved: 18.28713608,-66.03705597
Fetching weather for 42.39110184,-83.13121796 (2016)...
✅ Data retrieved: 42.39110184,-83.13121796
Fetching weather for 32.86539459,-96.868583

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\297163049.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9150 records for this batch

Processing batch 51 to 75 of 11835
Fetching weather for 18.02536774,-66.61303711 (2016)...
✅ Data retrieved: 18.02536774,-66.61303711
Fetching weather for 18.27383804,-66.37063599 (2016)...
✅ Data retrieved: 18.27383804,-66.37063599
Fetching weather for 18.2848053,-66.37059021 (2016)...
✅ Data retrieved: 18.2848053,-66.37059021
Fetching weather for 18.29496765,-66.37050629 (2016)...
✅ Data retrieved: 18.29496765,-66.37050629
Fetching weather for 18.25571251,-66.37050629 (2016)...
✅ Data retrieved: 18.25571251,-66.37050629
Fetching weather for 18.23466301,-66.37059784 (2016)...
✅ Data retrieved: 18.23466301,-66.37059784
Fetching weather for 18.26268196,-66.37049866 (2016)...
✅ Data retrieved: 18.26268196,-66.37049866
Fetching weather for 18.28279495,-66.37055969 (2016)...
✅ Data retrieved: 18.28279495,-66.37055969
Fetching weather for 18.27466202,-66.37058258 (2016)...
✅ Data retrieved: 18.27466202,-66.37058258
Fetching weather for 18.2689991,-66.37049

...

Saved 9150 records for this batch

Processing batch 10776 to 10800 of 11835
Fetching weather for 18.20073891,-66.0370636 (2016)...
✅ Data retrieved: 18.20073891,-66.0370636
Fetching weather for 18.29646301,-66.03705597 (2016)...
✅ Data retrieved: 18.29646301,-66.03705597
Fetching weather for 18.23650169,-66.03705597 (2016)...
✅ Data retrieved: 18.23650169,-66.03705597
Fetching weather for 18.23060036,-66.03705597 (2016)...
✅ Data retrieved: 18.23060036,-66.03705597
Fetching weather for 18.23447228,-66.03704834 (2016)...
✅ Data retrieved: 18.23447228,-66.03704834
Fetching weather for 18.2123127,-66.03705597 (2016)...
✅ Data retrieved: 18.2123127,-66.03705597
Fetching weather for 18.27945519,-66.03705597 (2016)...
✅ Data retrieved: 18.27945519,-66.03705597
Fetching weather for 18.25241852,-66.0370636 (2016)...
✅ Data retrieved: 18.25241852,-66.0370636
Fetching weather for 18.24131966,-66.0370636 (2016)...
✅ Data retrieved: 18.24131966,-66.0370636
Fetching weather for 18.20019722,-66.0370

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\297163049.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9150 records for this batch

Processing batch 11076 to 11100 of 11835
Fetching weather for 18.24691773,-66.37050629 (2016)...
✅ Data retrieved: 18.24691773,-66.37050629
Fetching weather for 18.24759674,-66.02526856 (2016)...
✅ Data retrieved: 18.24759674,-66.02526856
Fetching weather for 40.64011765,-73.94268036 (2016)...
✅ Data retrieved: 40.64011765,-73.94268036
Fetching weather for 18.29045868,-66.37049866 (2016)...
✅ Data retrieved: 18.29045868,-66.37049866
Fetching weather for 18.28666687,-66.37056732 (2016)...
✅ Data retrieved: 18.28666687,-66.37056732
Fetching weather for 18.27922058,-66.37059021 (2016)...
✅ Data retrieved: 18.27922058,-66.37059021
Fetching weather for 18.25029755,-66.03705597 (2016)...
✅ Data retrieved: 18.25029755,-66.03705597
Fetching weather for 18.22234154,-66.03705597 (2016)...
✅ Data retrieved: 18.22234154,-66.03705597
Fetching weather for 18.272295,-66.03704834 (2016)...
✅ Data retrieved: 18.272295,-66.03704834
Fetching weather for 18.29675102,-66.

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\297163049.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9150 records for this batch

Processing batch 11551 to 11575 of 11835
Fetching weather for 34.04514694,-118.2484818 (2016)...
✅ Data retrieved: 34.04514694,-118.2484818
Fetching weather for 38.40907288,-121.4195862 (2016)...
✅ Data retrieved: 38.40907288,-121.4195862
Fetching weather for 28.58658218,-81.28829193 (2016)...
✅ Data retrieved: 28.58658218,-81.28829193
Fetching weather for 34.00076294,-117.8856812 (2016)...
✅ Data retrieved: 34.00076294,-117.8856812
Fetching weather for 41.89596176,-87.69457245 (2016)...
✅ Data retrieved: 41.89596176,-87.69457245
Fetching weather for 18.20450401,-66.03704834 (2016)...
✅ Data retrieved: 18.20450401,-66.03704834
Fetching weather for 18.28610039,-66.03705597 (2016)...
✅ Data retrieved: 18.28610039,-66.03705597
Fetching weather for 18.26597595,-66.0370636 (2016)...
✅ Data retrieved: 18.26597595,-66.0370636
Fetching weather for 18.21594429,-66.03705597 (2016)...
✅ Data retrieved: 18.21594429,-66.03705597
Fetching weather for 18.27234268,-6

In [ ]:
# ================================
# Visual Crossing Weather Fetcher (2015)
# Batch processing (25 coordinates at a time)
# ================================



# --- STEP 1: Configuration ---
INPUT_CSV = "unique_lat_lon.csv"
OUTPUT_CSV = "visualcrossing_weather_2015.csv"
BATCH_SIZE = 25
YEAR = 2015

API_KEY = "BLRV9J7HVT4KS2DZ9KM4AUWWJ"



BASE_URL = (
    "https://weather.visualcrossing.com/VisualCrossingWebServices/rest/services/timeline/"
    "{lat},{lon}/{start_date}/{end_date}"
    "?unitGroup=us&elements=datetime,latitude,longitude,tempmax,tempmin,temp,humidity,precip,"
    "preciptype,snow,windspeed,cloudcover,solarradiation&include=days&key={api_key}&contentType=json"
)

# --- STEP 2: Function to fetch weather data for one location-year ---
def fetch_visualcrossing(lat, lon, year):
    start_date = f"{year}-01-01"
    end_date = f"{year}-12-31"
    url = BASE_URL.format(lat=lat, lon=lon, start_date=start_date, end_date=end_date, api_key=API_KEY)

    try:
        response = requests.get(url, timeout=60)
        response.raise_for_status()
        data = response.json()

        # Explicitly log if missing daily data
        if "days" not in data or not data["days"]:
            return f"EMPTY or MISSING daily section for {lat},{lon}"

        df = pd.json_normalize(data["days"])
        df["latitude"] = lat
        df["longitude"] = lon
        df["year"] = year
        return df

    except Exception as e:
        return f"ERROR: {e}"

# --- STEP 3: Load coordinates ---
df_coords = pd.read_csv(INPUT_CSV)
df_coords[['latitude', 'longitude']] = df_coords['lat_lon'].str.split(',', expand=True).astype(float)

# --- STEP 4: Batch processing (25 at a time) ---
num_coords = len(df_coords)
for start in range(0, num_coords, BATCH_SIZE):
    batch = df_coords.iloc[start:start + BATCH_SIZE]
    print(f"\nProcessing batch {start+1} to {start + len(batch)} of {num_coords}")

    batch_results = []
    for idx, row in batch.iterrows():
        lat = row["latitude"]
        lon = row["longitude"]

        print(f"Fetching weather for {lat},{lon} ({YEAR})...")
        result = fetch_visualcrossing(lat, lon, YEAR)

        if isinstance(result, pd.DataFrame):
            batch_results.append(result)
            print(f"✅ Data retrieved: {lat},{lon}")
        else:
            print(f"⚠️ Failed: {lat},{lon} -> {result}")

        time.sleep(1)  # To avoid hitting rate limits

    # Save results for this batch
    if batch_results:
        final_batch_df = pd.concat(batch_results, ignore_index=True)
        header_flag = not os.path.exists(OUTPUT_CSV)
        final_batch_df.to_csv(OUTPUT_CSV, mode="a", index=False, header=header_flag)
        print(f"Saved {len(final_batch_df)} records for this batch")

print("\nAll batches for 2015 processed and saved!")


Processing batch 1 to 25 of 11835
Fetching weather for 18.2514534,-66.03705597 (2015)...
✅ Data retrieved: 18.2514534,-66.03705597
Fetching weather for 18.27945137,-66.0370636 (2015)...
✅ Data retrieved: 18.27945137,-66.0370636
Fetching weather for 37.29223251,-121.881279 (2015)...
✅ Data retrieved: 37.29223251,-121.881279
Fetching weather for 34.12594605,-118.2910156 (2015)...
✅ Data retrieved: 34.12594605,-118.2910156
Fetching weather for 18.25376892,-66.03704834 (2015)...
✅ Data retrieved: 18.25376892,-66.03704834
Fetching weather for 43.01396942,-78.87906647 (2015)...
✅ Data retrieved: 43.01396942,-78.87906647
Fetching weather for 18.24253845,-66.03705597 (2015)...
✅ Data retrieved: 18.24253845,-66.03705597
Fetching weather for 25.92886925,-80.16287231 (2015)...
✅ Data retrieved: 25.92886925,-80.16287231
Fetching weather for 18.23322296,-66.03705597 (2015)...
✅ Data retrieved: 18.23322296,-66.03705597
Fetching weather for 37.77399063,-121.966629 (2015)...
✅ Data retrieved: 37.7739

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\3243265062.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 26 to 50 of 11835
Fetching weather for 18.26163292,-66.03705597 (2015)...
✅ Data retrieved: 18.26163292,-66.03705597
Fetching weather for 41.23545456,-75.86985779 (2015)...
✅ Data retrieved: 41.23545456,-75.86985779
Fetching weather for 18.27022362,-66.0370636 (2015)...
✅ Data retrieved: 18.27022362,-66.0370636
Fetching weather for 41.86886215,-84.57365418 (2015)...
✅ Data retrieved: 41.86886215,-84.57365418
Fetching weather for 33.90942383,-118.1253586 (2015)...
✅ Data retrieved: 33.90942383,-118.1253586
Fetching weather for 18.27526093,-66.0370636 (2015)...
✅ Data retrieved: 18.27526093,-66.0370636
Fetching weather for 41.86544037,-88.10990143 (2015)...
✅ Data retrieved: 41.86544037,-88.10990143
Fetching weather for 18.28713608,-66.03705597 (2015)...
✅ Data retrieved: 18.28713608,-66.03705597
Fetching weather for 42.39110184,-83.13121796 (2015)...
✅ Data retrieved: 42.39110184,-83.13121796
Fetching weather for 32.86539459,-96.868583

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\3243265062.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 51 to 75 of 11835
Fetching weather for 18.02536774,-66.61303711 (2015)...
✅ Data retrieved: 18.02536774,-66.61303711
Fetching weather for 18.27383804,-66.37063599 (2015)...
✅ Data retrieved: 18.27383804,-66.37063599
Fetching weather for 18.2848053,-66.37059021 (2015)...
✅ Data retrieved: 18.2848053,-66.37059021
Fetching weather for 18.29496765,-66.37050629 (2015)...
✅ Data retrieved: 18.29496765,-66.37050629
Fetching weather for 18.25571251,-66.37050629 (2015)...
✅ Data retrieved: 18.25571251,-66.37050629
Fetching weather for 18.23466301,-66.37059784 (2015)...
✅ Data retrieved: 18.23466301,-66.37059784
Fetching weather for 18.26268196,-66.37049866 (2015)...
✅ Data retrieved: 18.26268196,-66.37049866
Fetching weather for 18.28279495,-66.37055969 (2015)...
✅ Data retrieved: 18.28279495,-66.37055969
Fetching weather for 18.27466202,-66.37058258 (2015)...
✅ Data retrieved: 18.27466202,-66.37058258
Fetching weather for 18.2689991,-66.37049

...

Saved 9125 records for this batch

Processing batch 3051 to 3075 of 11835
Fetching weather for 18.25969124,-66.37050629 (2015)...
✅ Data retrieved: 18.25969124,-66.37050629
Fetching weather for 18.28088188,-66.37059021 (2015)...
✅ Data retrieved: 18.28088188,-66.37059021
Fetching weather for 18.23075676,-66.3706131 (2015)...
✅ Data retrieved: 18.23075676,-66.3706131
Fetching weather for 25.90393829,-80.25217438 (2015)...
✅ Data retrieved: 25.90393829,-80.25217438
Fetching weather for 18.26474571,-66.37058258 (2015)...
✅ Data retrieved: 18.26474571,-66.37058258
Fetching weather for 18.2357502,-66.37052918 (2015)...
✅ Data retrieved: 18.2357502,-66.37052918
Fetching weather for 33.99906921,-80.81486511 (2015)...
✅ Data retrieved: 33.99906921,-80.81486511
Fetching weather for 32.67300797,-117.0935211 (2015)...
✅ Data retrieved: 32.67300797,-117.0935211
Fetching weather for 37.96606445,-121.3069458 (2015)...
✅ Data retrieved: 37.96606445,-121.3069458
Fetching weather for 34.03588486,-118.0

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\3243265062.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 3151 to 3175 of 11835
Fetching weather for 40.64636612,-112.0324631 (2015)...
✅ Data retrieved: 40.64636612,-112.0324631
Fetching weather for 38.30499268,-85.81482697 (2015)...
✅ Data retrieved: 38.30499268,-85.81482697
Fetching weather for 35.87953186,-81.51202393 (2015)...
✅ Data retrieved: 35.87953186,-81.51202393
Fetching weather for 31.76372337,-106.4941864 (2015)...
✅ Data retrieved: 31.76372337,-106.4941864
Fetching weather for 36.70795059,-121.6539993 (2015)...
✅ Data retrieved: 36.70795059,-121.6539993
Fetching weather for 33.69275665,-84.61947632 (2015)...
✅ Data retrieved: 33.69275665,-84.61947632
Fetching weather for 42.06258011,-71.01766205 (2015)...
✅ Data retrieved: 42.06258011,-71.01766205
Fetching weather for 32.14844894,-110.9228516 (2015)...
✅ Data retrieved: 32.14844894,-110.9228516
Fetching weather for 33.45040512,-111.9264069 (2015)...
✅ Data retrieved: 33.45040512,-111.9264069
Fetching weather for 41.89629746,-8

C:\Users\Zaka and Family\AppData\Local\Temp\ipykernel_11568\3243265062.py:75: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_batch_df = pd.concat(batch_results, ignore_index=True)


Saved 9125 records for this batch

Processing batch 3201 to 3225 of 11835
Fetching weather for 39.22852707,-84.33337402 (2015)...
✅ Data retrieved: 39.22852707,-84.33337402
Fetching weather for 39.76057816,-84.33821869 (2015)...
✅ Data retrieved: 39.76057816,-84.33821869
Fetching weather for 33.97549439,-117.813179 (2015)...
✅ Data retrieved: 33.97549439,-117.813179
Fetching weather for 36.02261353,-115.172287 (2015)...
✅ Data retrieved: 36.02261353,-115.172287
Fetching weather for 37.29937744,-121.8589783 (2015)...
✅ Data retrieved: 37.29937744,-121.8589783
Fetching weather for 42.77547073,-83.3214798 (2015)...
✅ Data retrieved: 42.77547073,-83.3214798
Fetching weather for 34.20328903,-118.5709763 (2015)...
✅ Data retrieved: 34.20328903,-118.5709763
Fetching weather for 41.89460754,-87.77870178 (2015)...
✅ Data retrieved: 41.89460754,-87.77870178
Fetching weather for 39.11119843,-76.48913574 (2015)...
✅ Data retrieved: 39.11119843,-76.48913574
Fetching weather for 35.80294418,-78.6081